In [ ]:
!pip install gensim


In [ ]:
!pip install rouge-score


In [ ]:
pip install scikit-learn nltk


In [ ]:
!pip install textblob

In [ ]:
import pandas as pd
import nltk
import gensim
import numpy as np
from nltk.corpus import stopwords
from nltk.tokenize import sent_tokenize, word_tokenize
from gensim import corpora
from collections import Counter
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity
from heapq import nlargest
from rouge_score import rouge_scorer

In [ ]:
# Download necessary NLTK data files
nltk.download('punkt')
nltk.download('stopwords')
nltk.download('averaged_perceptron_tagger')

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /root/nltk_data...
[nltk_data]   Unzipping taggers/averaged_perceptron_tagger.zip.


True

In [ ]:
# Load dataset
df = pd.read_csv('/content/abcnews-date-text.csv')
df

publish_date                                      headline_text
0           20030219  aba decides against community broadcasting lic...
1           20030219     act fire witnesses must be aware of defamation
2           20030219     a g calls for infrastructure protection summit
3           20030219           air nz staff in aust strike for pay rise
4           20030219      air nz strike to affect australian travellers
...              ...                                                ...
149239      20050304   campaign to increase awareness of new road speed
149240      20050304                 china budgets for military upgrade
149241      20050304              china condemns us human rights record
149242      20050304  china restates opposition to taiwanese indepen...
149243      20050304                                   china urges calm

[149244 rows x 2 columns]

In [ ]:
df.head()

publish_date                                      headline_text
0      20030219  aba decides against community broadcasting lic...
1      20030219     act fire witnesses must be aware of defamation
2      20030219     a g calls for infrastructure protection summit
3      20030219           air nz staff in aust strike for pay rise
4      20030219      air nz strike to affect australian travellers

In [ ]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 149244 entries, 0 to 149243
Data columns (total 2 columns):
 #   Column         Non-Null Count   Dtype 
---  ------         --------------   ----- 
 0   publish_date   149244 non-null  int64 
 1   headline_text  149244 non-null  object
dtypes: int64(1), object(1)
memory usage: 2.3+ MB


In [ ]:
df.columns

Index(['publish_date', 'headline_text'], dtype='object')

In [ ]:
reindexed_data = df['headline_text']
reindexed_data.index = df['publish_date']

preprocess and define summary()


Frequency based approach

In [ ]:
# Define the generate_summary function
def generate_summary(text, n):
    # Tokenize the text into individual sentences
    sentences = sent_tokenize(text)

    # Tokenize each sentence into individual words and remove stopwords
    stop_words = set(stopwords.words('english'))
    words = [word.lower() for word in word_tokenize(text) if word.lower() not in stop_words and word.isalnum()]

    # Compute the frequency of each word
    word_freq = Counter(words)

    # Compute the score for each sentence based on the frequency of its words
    sentence_scores = {}
    for sentence in sentences:
        sentence_words = [word.lower() for word in word_tokenize(sentence) if word.lower() not in stop_words and word.isalnum()]
        sentence_score = sum([word_freq[word] for word in sentence_words])
        if len(sentence_words) < 20:  # You can adjust this threshold as needed
            sentence_scores[sentence] = sentence_score

    # Select the top n sentences with the highest scores
    summary_sentences = sorted(sentence_scores, key=sentence_scores.get, reverse=True)[:n]
    summary = ' '.join(summary_sentences)

    return summary


In [ ]:
grouped = reindexed_data.groupby(reindexed_data.index).apply(' '.join).reset_index(name='headline_text')


In [ ]:
# Apply the summarization function to each group
grouped['summary'] = grouped['headline_text'].apply(lambda x: generate_summary(x, 5))  # Set to 5 sentences

In [ ]:
# Get the most recent 5 dates
recent_dates = grouped['publish_date'].drop_duplicates().sort_values(ascending=False).head(5)

In [ ]:

# Display summaries with additional debugging information
for date, group in grouped.groupby('publish_date'):
    summary = group['summary'].iloc[0]
    print(f"Headlines for {date}: {group['headline_text'].iloc[0]}")
    print("-" * 5)



Headlines for 20030219: aba decides against community broadcasting licence act fire witnesses must be aware of defamation a g calls for infrastructure protection summit air nz staff in aust strike for pay rise air nz strike to affect australian travellers ambitious olsson wins triple jump antic delighted with record breaking barca aussie qualifier stosur wastes four memphis match aust addresses un security council over iraq australia is locked into war timetable opp australia to contribute 10 million in aid to iraq barca take record as robson celebrates birthday in bathhouse plans move ahead big hopes for launceston cycling championship big plan to boost paroo water supplies blizzard buries united states in bills brigadier dismisses reports troops harassed in british combat troops arriving daily in kuwait bryant leads lakers to double overtime win bushfire victims urged to see centrelink businesses should prepare for terrorist attacks calleri avenges final defeat to eliminate massu cal

extrraction(td-idf)

In [ ]:

def generate_summary(text, n):
    # Tokenize the text into individual sentences
    sentences = sent_tokenize(text)

    # Create the TF-IDF matrix
    vectorizer = TfidfVectorizer(stop_words='english')
    tfidf_matrix = vectorizer.fit_transform(sentences)

    # Compute the cosine similarity between each sentence and the document
    cosine_similarities = cosine_similarity(tfidf_matrix, tfidf_matrix).mean(axis=1)

    # Select the top n sentences with the highest scores
    summary_sentences = nlargest(n, range(len(cosine_similarities)), key=cosine_similarities.__getitem__)

    # Join the selected sentences to form the summary
    summary_tfidf = ' '.join([sentences[i] for i in sorted(summary_sentences)])

    return summary_tfidf

In [ ]:
# Apply the summarization function to each row in the DataFrame
df['summary'] = df['headline_text'].apply(lambda x: generate_summary(x, 5))  # Set to 5 sentences



In [ ]:
 #Display the summaries
for index, row in df.iterrows():
    print(f"Date: {row['publish_date']}")
    print(f"Summary: {row['summary']}\n")

Streaming output truncated to the last 5000 lines.
Summary: council allows sign trial

Date: 20050224
Summary: council offers revellers late night bus

Date: 20050224
Summary: councils to feel federal funds cut

Date: 20050224
Summary: court dismisses pipeline legal row

Date: 20050224
Summary: crash probe finds black hawk hit tree

Date: 20050224
Summary: criticism of iraq deployment confused howard

Date: 20050224
Summary: csiro building evacuated after gas leak

Date: 20050224
Summary: dajka recalled to australian team

Date: 20050224
Summary: decision looms on rail line move

Date: 20050224
Summary: disability advocacy group asks for 19m

Date: 20050224
Summary: doyle hits back at liberal rats

Date: 20050224
Summary: dpp considers contempt charges over article

Date: 20050224
Summary: dr congo plague outbreak spreads

Date: 20050224
Summary: driver to face court over high blood alcohol

Date: 20050224
Summary: drogba dismissal sours mourinhos barca return

Date: 20050224
Summary: 

Evaluation function

In [ ]:

# Define the evaluation function
def evaluate_rouge(reference_text, summary_text):
    rouge = Rouge()
    scores = rouge.get_scores(reference_text, summary_text)
    return scores[0]['rouge-1']['f']

In [ ]:
# Initialize a list to store ROUGE scores
rouge_scores = []

# Calculate ROUGE scores for each summary and append to the list
for index, row in df.iterrows():
    generated_summary = row['summary']
    # Ensure reference_summary is a string
    if not isinstance(reference_summary, str):
        reference_summary = str(reference_summary)
    rouge_score = evaluate_rouge(reference_summary, generated_summary)
    rouge_scores.append(rouge_score)

# Calculate average ROUGE-1 F1 score
average_rouge_score = sum(rouge_scores) / len(rouge_scores)

# Print the average ROUGE-1 F1 score
print(f"Average ROUGE-1 F1 Score for the dataset: {average_rouge_score:.4f}")

Average ROUGE-1 F1 Score for the dataset: 0.0225
